# Libs

In [1]:
import os
while os.getcwd().split('\\')[-1] != 'master-llm-rag-vnlaw':
    os.chdir('..')
    print(os.getcwd())

d:\DANG NHI\repos\master-llm-rag-vnlaw


In [ ]:
import os
import glob
import ollama
import chromadb
from chromadb import Settings, EmbeddingFunction, Embeddings

import torch
from transformers import AutoTokenizer, AutoModel

In [19]:
base_model_id = "FacebookAI/xlm-roberta-base"
trained_model_path = "trained_embedding_model/"
data_path = "data/"

In [ ]:
model = AutoModel.from_pretrained(trained_model_path)
model.eval()
tokenizer = AutoTokenizer.from_pretrained(base_model_id)

In [9]:
class MyEmbeddingFunction(EmbeddingFunction):
    def __init__(self, model, tokenizer, max_length=512):
        self.model = model
        self.tokenizer = tokenizer
        self.max_length = max_length


    def embed_documents(self, texts):
        inputs = self.tokenizer(texts, 
                                padding=True, 
                                max_length=self.max_length, 
                                return_tensors="pt")
        with torch.no_grad():
            embeddings = self.model(**inputs).pooler_output
        return embeddings.numpy()

    def embed_query(self, text):
        inputs = self.tokenizer(text, return_tensors="pt")
        with torch.no_grad():
            embeddings = self.model(**inputs).last_hidden_state.mean(dim=1)
        return embeddings.numpy()

In [10]:
myembed = MyEmbeddingFunction(model, tokenizer)

In [14]:
output = myembed.embed_documents(["Hello world!"])

d:\miniconda3\envs\llm-mining\lib\site-packages\transformers\tokenization_utils_base.py:2718: UserWarning: `max_length` is ignored when `padding`=`True` and there is no truncation strategy. To pad to max length, use `padding='max_length'`.
  warnings.warn(


In [16]:
output.shape

(1, 768)

# Add to db

In [ ]:
client = chromadb.Client(
    Settings(chroma_db_impl="duckdb+parquet",
             persist_directory="chromadb/"))

In [ ]:
import json
files = os.listdir(data_path)
for file in files:
    with open(os.path.join(data_path, file), 'r', encoding='utf-8') as f:
        data = json.load(f)
    for document in data:
        url = document['url']
        name = document['name']
        content = document['content']
        # Check if the document already exists in the collection
        collection = client.get_or_create_collection(name=name)
        # Check if the document is already in the collection
        existing_documents = collection.query(where={"url": url})
        if existing_documents['documents']:
            print(f"Document with URL {url} already exists in the collection {name}. Skipping.")
            continue
        # Add the document to the collection

        content = "\n".join(content)
        chunks = text

        collection.add(
            documents=[content],
            metadatas=[{"url": url, "name": name}],
            ids=[name + "- {i}"],
            embeddings=myembed.embed_documents([content])
        )
        
        
    break

In [21]:
data

[{'url': 'https://dulieuphapluat.vn/van-ban/bao-hiem-van-ban/nghi-quyet-062024nq-hdnd-ve-muc-gia-dich-vu-kham-benh-chua-benh-khong-thuoc-pham-vi-thanh-toan-cua-quy-bao-hiem-y-te-ma-khong-phai-la-dich-vu-kham-benh-chua-benh-theo-yeu-cau-tai-cac-co-so-kham-benh-chua-benh-cua-nha-nuoc-tren-dia-ban-tinh-khanh-hoa-1197970.html',
  'name': 'Nghị quyết 06/2024/NQ-HĐND',
  'content': ['HỘI ĐỒNG NHÂN DÂN TỈNH KHÁNH HÒA \n Số: 06/2024/NQ-HĐND \n Khánh Hòa, ngày 12 tháng 7 năm 2024',
   'NGHỊ QUYẾT',
   'VỀ VIỆC BAN HÀNH MỨC GIÁ DỊCH VỤ KHÁM BỆNH, CHỮA BỆNH KHÔNG THUỘC PHẠM VI THANH TOÁN CỦA QUỸ BẢO HIỂM Y TẾ MÀ KHÔNG PHẢI LÀ DỊCH VỤ KHÁM BỆNH, CHỮA BỆNH THEO YÊU CẦU TẠI CÁC CƠ SỞ KHÁM BỆNH, CHỮA BỆNH CỦA NHÀ NƯỚC TRÊN ĐỊA BÀN TỈNH KHÁNH HÒA',
   'HỘI ĐỒNG NHÂN DÂN TỈNH KHÁNH HÒA KHÓA VII, KỲ HỌP THỨ 14',
   'Căn cứ Luật Tổ chức chính quyền địa phương ngày 19 tháng 6 năm 2015;',
   'Căn cứ Luật sửa đổi, bổ sung một số điều của Luật Tổ chức Chính phủ và Luật tổ chức chính quyền địa phương ngày 22 